# Unternehmensregister

## Fetch Auszug

In [1]:
import os
import glob

In [2]:
def wait_for_download_condition(
    path: str, num_files: int, pattern: str = "*.xml"
) -> bool:
    return len(glob.glob1(path, pattern)) > num_files


def get_num_files(path: str, pattern: str = "*.xml") -> int:
    return len(glob.glob1(path, pattern))


def rename_latest_file(path: str, filename: str, pattern: str = "*.xml"):
    list_of_files = [os.path.join(path, file) for file in glob.glob1(path, pattern)]
    latest_download = max(list_of_files, key=os.path.getctime)
    os.rename(latest_download, os.path.join(path, filename))

In [3]:
from tqdm import tqdm
from pathlib import Path

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

search_query = "A*"

options = webdriver.ChromeOptions()

download_path = str(Path(Path.cwd() / "data" / "Unternehmensregister"))
print(download_path)

preferences = {
    "profile.default_content_settings.popups": 0,
    "safebrowsing.enabled": True,
    "download": {
        "directory_upgrade": True,
        "prompt_for_download": False,
        "extensions_to_open": "",
        "default_directory": download_path,
    },
}
options.add_argument("--headless=new")
options.add_experimental_option("prefs", preferences)

driver = webdriver.Chrome(options=options)

driver.get("https://www.unternehmensregister.de/ureg/")
# Accept Cookies
driver.find_elements(
    By.XPATH, '//button[text()="Nur technisch notwendige Cookies akzeptieren"]'
)[0].click()
# Enter search query
driver.find_elements(By.ID, "globalSearchForm:extendedResearchCompanyName")[
    0
].send_keys(search_query)
# Trigger search
driver.find_elements(By.ID, "globalSearchForm:btnExecuteSearchOld")[0].click()
# Wait for results
wait = WebDriverWait(driver, 5)
wait.until(
    lambda driver: driver.current_url != "https://www.unternehmensregister.de/ureg/"
)

num_pages = int(
    driver.find_element(By.XPATH, '//*[@class="page_count"]').text.split(" ")[0]
)

processed_companies = []

for page_index in tqdm(range(num_pages)):
    # Find all "Registerinformationen"
    companies_tab = driver.find_elements(
        By.LINK_TEXT, "Registerinformationen des Registergerichts"
    )
    company_names = [
        elem.text
        for elem in driver.find_elements(
            By.XPATH, '//div[@class="company_result"]/span/b'
        )
    ]
    for index, company_link in enumerate(companies_tab):
        company_name = company_names[index]
        if company_name in processed_companies:
            continue
        # Go to intermediary page
        company_link.click()
        # Trigger next redirect
        driver.find_element(By.LINK_TEXT, "Registerinformationen anzeigen").click()
        # Trigger SI download
        driver.find_element(By.LINK_TEXT, "SI").click()
        # Show shopping cart - TODO evaluate restructuring behaviour by filling cart first and then bulk downloading
        wait.until(
            EC.visibility_of_element_located((By.LINK_TEXT, "Dokumentenkorb ansehen"))
        )
        driver.find_element(By.LINK_TEXT, "Dokumentenkorb ansehen").click()
        # Get document
        xpath = "//input[@type='submit']"
        elems = driver.find_elements(By.TAG_NAME, "input")
        elems[-2].click()

        wait.until(
            EC.visibility_of_element_located((By.ID, "paymentFormOverview:btnNext"))
        )
        driver.find_element(By.ID, "paymentFormOverview:btnNext").click()

        wait.until(
            EC.visibility_of_element_located((By.LINK_TEXT, "Zum Dokumentenkorb"))
        )
        driver.find_element(By.LINK_TEXT, "Zum Dokumentenkorb").click()

        num_files = get_num_files("./data/Unternehmensregister/")
        driver.find_element(By.CLASS_NAME, "download-wrapper").click()

        try:
            wait.until(
                lambda x: wait_for_download_condition(
                    "./data/Unternehmensregister/", num_files
                )
            )
            rename_latest_file(
                "./data/Unternehmensregister/",
                f"{company_name.replace(' ', '_').replace('/','_')}.xml",
            )
            processed_companies.append(company_name)
        except:
            print(f"Could not process {company_name}")
        for i in range(6):
            driver.back()
    driver.find_element(By.XPATH, '//*[@class="fas fa-angle-right"]').click()
driver.close()
print(processed_companies)

c:\Users\trist\Documents\Code\M.Sc\aki_prj23_transparenzregister\Jupyter\API-tests\Unternehmensregister\data\Unternehmensregister


  0%|          | 0/4192 [00:00<?, ?it/s]

Could not process A. Gradmann GmbH & Co. KG
Could not process A + P Baumaschinen GmbH & Co. KG
Could not process A. Sluka-Verwaltungsgesellschaft mit beschränkter Haftung
Could not process A + W. Sahm Bedachungs-GmbH


  0%|          | 1/4192 [00:48<56:17:10, 48.35s/it]

Could not process A + W. Sahm Bedachungs-GmbH
Could not process A + M Verwaltungs-GmbH
Could not process A. Frauenrath Landschaftsbau GmbH & Co. KG.


  0%|          | 2/4192 [01:29<51:30:19, 44.25s/it]

Could not process A. Frauenrath Landschaftsbau GmbH & Co. KG.
Could not process a s k - Kunststoffe GmbH


  0%|          | 2/4192 [02:09<75:11:08, 64.60s/it]


KeyboardInterrupt: 

## Analyze Auszug

In [6]:
import os

files = os.listdir("./data/Unternehmensregister")
files

['A&A_Amini_Art_GmbH.json',
 'A&A_Amini_Art_GmbH.xml',
 'A&A_Immo_GmbH.json',
 'A&A_Immo_GmbH.xml',
 'A&P_AUDITING_GmbH_Wirtschaftsprüfungsgesellschaft.json',
 'A&P_AUDITING_GmbH_Wirtschaftsprüfungsgesellschaft.xml',
 'A&QUA_gemeinnützige_Gesellschaft_für_Arbeit_u._Qualifizierung_mbH.json',
 'A&QUA_gemeinnützige_Gesellschaft_für_Arbeit_u._Qualifizierung_mbH.xml',
 'a+b_Asphalt-_und_Betonmischwerke_GmbH_&_Co._KG.json',
 'a+b_Asphalt-_und_Betonmischwerke_GmbH_&_Co._KG.xml',
 'a+b_Verwaltungsgesellschaft_mbH.json',
 'a+b_Verwaltungsgesellschaft_mbH.xml',
 'A+E_Beteiligungs-_und_Handels-GmbH.json',
 'A+E_Beteiligungs-_und_Handels-GmbH.xml',
 'A+W_Systemhaus_GmbH.json',
 'A+W_Systemhaus_GmbH.xml',
 'A-S-D_Kfz-Teile-Handel_GmbH.json',
 'A-S-D_Kfz-Teile-Handel_GmbH.xml',
 'A-TEAM_Industrielles_Roboterschweißen_GmbH.json',
 'A-TEAM_Industrielles_Roboterschweißen_GmbH.xml',
 'A.C.C._Funk_Taxi_&_Minicar_e.K..json',
 'A.C.C._Funk_Taxi_&_Minicar_e.K..xml',
 'a.c.k._aqua_concept_GmbH_Karlsruhe.json

In [7]:
import json
import xmltodict


def transform_xml_to_json(source_dir: str, target_dir: str):
    for file in glob.glob1(source_dir, "*.xml"):
        source_path = os.path.join(source_dir, file)
        target_path = os.path.join(target_dir, file.replace(".xml", ".json"))

        with open(source_path, "r", encoding="utf-8") as source_file:
            data = xmltodict.parse(source_file.read().encode())
            with open(target_path, "w", encoding="utf-8") as json_file:
                json_file.write(json.dumps(data))


transform_xml_to_json("./data/Unternehmensregister/", "./data/Unternehmensregister/")

In [8]:
for file in glob.glob1("./data/Unternehmensregister/", "*.json"):
    path = os.path.join("./data/Unternehmensregister/", file)
    with open(path, "r", encoding="utf-8") as file_object:
        data = json.loads(file_object.read())

In [19]:
from models.Company import Company


def parse_stakeholder(data: dict) -> list:
    if "Natuerliche_Person" in data["Beteiligter"]:
        return {
            "name": {
                "firstname": data["Beteiligter"]["Natuerliche_Person"]["Voller_Name"][
                    "Vorname"
                ],
                "lastname": data["Beteiligter"]["Natuerliche_Person"]["Voller_Name"][
                    "Nachname"
                ],
            },
            "date_of_birth": data["Beteiligter"]["Natuerliche_Person"]["Geburt"][
                "Geburtsdatum"
            ]
            if "Geburt" in data["Beteiligter"]["Natuerliche_Person"]
            else None,
            "location": {
                "city": data["Beteiligter"]["Natuerliche_Person"]["Anschrift"]["Ort"]
            },
            "role": data["Rolle"]["Rollenbezeichnung"]["content"],
        }
    if "Organisation" in data["Beteiligter"]:
        return {
            "role": "Organisation",
            "description": data["Beteiligter"]["Organisation"]["Bezeichnung"][
                "Bezeichnung_Aktuell"
            ],
            "location": {
                "city": data["Beteiligter"]["Organisation"]["Anschrift"]["Ort"],
                "street": data["Beteiligter"]["Organisation"]["Anschrift"]["Strasse"]
                if "Strasse" in data["Beteiligter"]["Organisation"]["Anschrift"]
                else None,
                "house_number": data["Beteiligter"]["Organisation"]["Anschrift"][
                    "Hausnummer"
                ]
                if "Hausnummer" in data["Beteiligter"]["Organisation"]["Anschrift"]
                else None,
                "zip_code": data["Beteiligter"]["Organisation"]["Anschrift"][
                    "Postleitzahl"
                ],
            },
        }


def map_unternehmensregister_json(data: dict) -> dict:
    result = {"relationships": []}

    result["id"] = {
        "hr_number": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
            "Instanzdaten"
        ]["Aktenzeichen"],
        "district_court": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
            "Beteiligung"
        ][1]["Beteiligter"]["Organisation"]["Bezeichnung"]["Bezeichnung_Aktuell"],
    }
    result["name"] = data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
        "Rechtstraeger"
    ]["Bezeichnung"]["Bezeichnung_Aktuell"]

    result["location"] = {
        "city": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Ort"],
        "zip_code": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Postleitzahl"],
        "street": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Strasse"]
        if "Strasse"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]
        else None,
        "house_number": data["XJustiz_Daten"]["Fachdaten_Register"][
            "Basisdaten_Register"
        ]["Rechtstraeger"]["Anschrift"]["Hausnummer"]
        if "Hausnummer"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]
        else None,
    }
    result["last_update"] = data["XJustiz_Daten"]["Fachdaten_Register"]["Auszug"][
        "letzte_Eintragung"
    ]

    for i in range(
        2, len(data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"])
    ):
        people = parse_stakeholder(
            data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][i]
        )
        result["relationships"].append(people)
    return Company(**result)

In [22]:
import json
import dataclasses

for file in glob.glob1("./data/Unternehmensregister/", "*.json"):
    path = os.path.join("./data/Unternehmensregister/", file)
    with open(path, "r", encoding="utf-8") as file_object:
        data = json.loads(file_object.read())

        company: Company = map_unternehmensregister_json(data)
        print(company.name)

        name = (
            company.name.replace(" ", "_")
            .replace("/", "_")
            .replace('"', "")
            .replace("|", "_")
        )
        with open(
            f"./data/Unternehmensregister/export/{name}.json", "w+", encoding="utf-8"
        ) as export_file:
            json.dump(dataclasses.asdict(company), export_file, ensure_ascii=False)

A&A Amini Art GmbH
A&A Immo GmbH
A&P AUDITING GmbH Wirtschaftsprüfungsgesellschaft
A&QUA gemeinnützige Gesellschaft für Arbeit u. Qualifizierung mbH
a+b Asphalt- und Betonmischwerke GmbH & Co. KG
a+b Verwaltungsgesellschaft mbH
A+E Beteiligungs- und Handels-GmbH
A+W Systemhaus GmbH
A-S-D Kfz-Teile-Handel GmbH
A-TEAM Industrielles Roboterschweißen GmbH
A.C.C. Funk Taxi & Minicar e.K.
a.c.k. aqua concept GmbH Karlsruhe
A.C. Weiss GmbH & Co. KG
A.D.S. OHG
A.D. Glas- und Gebäudereinigung e.K.
A.E. Z-Line Taxi - und Shuttle-Service e.K.
A.F.Z. Automatisierung, Fördern, Zuführen GmbH
A.G. Zentral Michael Greising e.K.
A.H. Steuerberatungsgesellschaft mbH
A.I.V. SERVICES GmbH
A.I. Kommanditist-Gesellschaft mbH
A.KIein Immobilien KG
A.L.G. Christian Schmelzer
A.L.S. Architektonische Licht-Systeme GmbH
A.M.G. Motorenbau Hans Werner Aufrecht
A.M.P. Athos GmbH
A.N. Gartenbau GmbH
A.Q.U.A Services KG
A.R.S. GmbH Süd, Alt und Reststoffverwertung
A.S.G. Industrielackierungen GmbH
A.S.S. bikes and pa